# predicting brooklyn food price

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!pip install geopy 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!pip install folium==0.5.0
import folium # map rendering library

In [2]:
with open("nyu_2451_34572-geojson.json") as datafile:
  NYdata = json.load(datafile)

In [3]:
NYdata=NYdata['features']

In [4]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [5]:
for data in NYdata:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [6]:
neighborhoods['Borough'].unique()

array(['Bronx', 'Manhattan', 'Brooklyn', 'Queens', 'Staten Island'],
      dtype=object)

In [7]:
def label_borough (row):
    if row['Borough'] == 'Bronx' :
      return 2
    if row['Borough'] == 'Manhattan' :
      return 1
    if row['Borough'] == 'Brooklyn' :
      return 3
    if row['Borough'] == 'Queens' :
      return 4
    if row['Borough'] == 'Staten Island' :
      return 5
    return 'Other'

In [8]:
neighborhoods['Borough ID']=neighborhoods.apply (lambda row: label_borough(row), axis=1)
neighborhoods

Borough               Neighborhood   Latitude  Longitude  \
0            Bronx                  Wakefield  40.894705 -73.847201   
1            Bronx                 Co-op City  40.874294 -73.829939   
2            Bronx                Eastchester  40.887556 -73.827806   
3            Bronx                  Fieldston  40.895437 -73.905643   
4            Bronx                  Riverdale  40.890834 -73.912585   
5            Bronx                Kingsbridge  40.881687 -73.902818   
6        Manhattan                Marble Hill  40.876551 -73.910660   
7            Bronx                   Woodlawn  40.898273 -73.867315   
8            Bronx                    Norwood  40.877224 -73.879391   
9            Bronx             Williamsbridge  40.881039 -73.857446   
10           Bronx                 Baychester  40.866858 -73.835798   
11           Bronx             Pelham Parkway  40.857413 -73.854756   
12           Bronx                City Island  40.847247 -73.786488   
13           Bronx               Bedford Park  40.870185 -73.885512   
14           Bronx         University Heights  40.855727 -73.910416   
15           Bronx             Morris Heights  40.847898 -73.919672   
16           Bronx                    Fordham  40.860997 -73.896427   
17           Bronx               East Tremont  40.842696 -73.887356   
18           Bronx                 West Farms  40.839475 -73.877745   
19           Bronx               High  Bridge  40.836623 -73.926102   
20           Bronx                    Melrose  40.819754 -73.909422   
21           Bronx                 Mott Haven  40.806239 -73.916100   
22           Bronx                Port Morris  40.801664 -73.913221   
23           Bronx                   Longwood  40.815099 -73.895788   
24           Bronx                Hunts Point  40.809730 -73.883315   
25           Bronx                 Morrisania  40.823592 -73.901506   
26           Bronx                  Soundview  40.821012 -73.865746   
27           Bronx               Clason Point  40.806551 -73.854144   
28           Bronx                Throgs Neck  40.815109 -73.816350   
29           Bronx               Country Club  40.844246 -73.824099   
30           Bronx                Parkchester  40.837938 -73.856003   
31           Bronx         Westchester Square  40.840619 -73.842194   
32           Bronx                   Van Nest  40.843608 -73.866299   
33           Bronx                Morris Park  40.847549 -73.850402   
34           Bronx                    Belmont  40.857277 -73.888452   
35           Bronx             Spuyten Duyvil  40.881395 -73.917190   
36           Bronx            North Riverdale  40.908543 -73.904531   
37           Bronx                 Pelham Bay  40.850641 -73.832074   
38           Bronx              Schuylerville  40.826580 -73.826203   
39           Bronx             Edgewater Park  40.821986 -73.813885   
40           Bronx                Castle Hill  40.819014 -73.848027   
41           Bronx                  Olinville  40.871371 -73.863324   
42           Bronx             Pelham Gardens  40.862966 -73.841612   
43           Bronx                  Concourse  40.834284 -73.915589   
44           Bronx                  Unionport  40.829774 -73.850535   
45           Bronx                   Edenwald  40.884561 -73.848083   
46        Brooklyn                  Bay Ridge  40.625801 -74.030621   
47        Brooklyn                Bensonhurst  40.611009 -73.995180   
48        Brooklyn                Sunset Park  40.645103 -74.010316   
49        Brooklyn                 Greenpoint  40.730201 -73.954241   
50        Brooklyn                  Gravesend  40.595260 -73.973471   
51        Brooklyn             Brighton Beach  40.576825 -73.965094   
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186   
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438   
54        Brooklyn                   Flatbush  40.636326 -73.958401   
55        Brooklyn              Cro

In [9]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [10]:
colors_array = cm.rainbow(np.linspace(0, 1, 6))
rainbow = [colors.rgb2hex(i) for i in colors_array]

### different colors represent different boroughs

In [11]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood, ID in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood'], neighborhoods['Borough ID']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color=rainbow[ID],
        fill=True,
        fill_color=rainbow[ID],
        fill_opacity=0.4,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [12]:
CLIENT_ID = 'JLOLYTL3R3JH1JD3ODLANEZCG53BGLPV4ISOWFQ54XLTVQTD' # your Foursquare ID
CLIENT_SECRET = 'LSKYXTJROVH3QIOAPPRSYKZIVFVP4YGIVNVYPGVTMYY5WQVY' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

### define a function that gets venue details depending on different price ranges

In [13]:
def getNearbyVenues(names, latitudes, longitudes, price_range, radius=500,LIMIT=50):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&section={}&price={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT,
            'food',
            price_range)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

## Brooklyn neighbourhood food venues data

In [14]:
Brooklyn=neighborhoods[neighborhoods['Borough']== 'Brooklyn'].reset_index(drop=True)

In [15]:
Brooklyn.shape

(70, 5)

### first, find venues in the cheapest price range

In [16]:
venues = getNearbyVenues(names=Brooklyn['Neighborhood'],
                                   latitudes=Brooklyn['Latitude'],
                                   longitudes=Brooklyn['Longitude'],
                                   price_range=1
                                  )

Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Ditmas Park
Wingate
Rugby
Remsen Village
New Lots
Paerdegat Basin
Mill Basin
Fulton Ferry
Vinegar Hill
Weeksville
Broadway Junction
Dumbo
Homecrest
Highland Park
Madison
Erasmus


In [17]:
venues.drop_duplicates(inplace=True)

In [18]:
venues['Venue Category'].unique()

array(['Bagel Shop', 'Sandwich Place', 'Thai Restaurant',
       'Chinese Restaurant', 'Fast Food Restaurant', 'Donut Shop',
       'Mexican Restaurant', 'Bakery', 'Deli / Bodega', 'Gastropub',
       'Pizza Place', 'Breakfast Spot', 'Caribbean Restaurant', 'Diner',
       'Restaurant', 'Taco Place', 'Café', 'Korean Restaurant',
       'Falafel Restaurant', 'Fried Chicken Joint',
       'Middle Eastern Restaurant', 'Burger Joint',
       'Latin American Restaurant', 'Hot Dog Joint', 'Food Truck',
       'Seafood Restaurant', 'Vietnamese Restaurant',
       'Italian Restaurant', 'Asian Restaurant',
       'Southern / Soul Food Restaurant', 'Burrito Place',
       'Cuban Restaurant', 'Dumpling Restaurant', 'Indian Restaurant',
       'Food', 'American Restaurant', 'Tibetan Restaurant'], dtype=object)

In [19]:
# display the venues on a map
# create map of New York using latitude and longitude values
map_venues = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood, name in zip(venues['Venue Latitude'], venues['Venue Longitude'], venues['Neighborhood'], venues['Venue']):
    label = '{}, {}'.format(neighborhood, name)
    label = folium.Popup(label, parse_html=True)
    
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=0.4,
        parse_html=False).add_to(map_venues)  
    
map_venues

In [20]:
venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Bay Ridge              40.625801              -74.030621   
1    Bay Ridge              40.625801              -74.030621   
2    Bay Ridge              40.625801              -74.030621   
3    Bay Ridge              40.625801              -74.030621   
4    Bay Ridge              40.625801              -74.030621   

                Venue  Venue Latitude  Venue Longitude        Venue Category  
0           Bagel Boy       40.627896       -74.029335            Bagel Shop  
1            Cinnabon       40.623156       -74.031459        Sandwich Place  
2  My Thai Restaurant       40.629160       -74.028689       Thai Restaurant  
3      Pearl of China       40.624631       -74.030301    Chinese Restaurant  
4          McDonald's       40.622159       -74.027731  Fast Food Restaurant

### add a price range column to this dataframe

In [21]:
venues['Price Range']=1

In [22]:
venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Bay Ridge              40.625801              -74.030621   
1    Bay Ridge              40.625801              -74.030621   
2    Bay Ridge              40.625801              -74.030621   
3    Bay Ridge              40.625801              -74.030621   
4    Bay Ridge              40.625801              -74.030621   

                Venue  Venue Latitude  Venue Longitude        Venue Category  \
0           Bagel Boy       40.627896       -74.029335            Bagel Shop   
1            Cinnabon       40.623156       -74.031459        Sandwich Place   
2  My Thai Restaurant       40.629160       -74.028689       Thai Restaurant   
3      Pearl of China       40.624631       -74.030301    Chinese Restaurant   
4          McDonald's       40.622159       -74.027731  Fast Food Restaurant   

   Price Range  
0            1  
1            1  
2            1  
3            1  
4            1

### now write a loop to get the other price ranges, and combine the dataframes into one

In [23]:
venues_priced=pd.DataFrame()

for i in range (4):
    venues = getNearbyVenues(names=Brooklyn['Neighborhood'],
                                   latitudes=Brooklyn['Latitude'],
                                   longitudes=Brooklyn['Longitude'],
                                   price_range=i+1
                                  )
    venues.drop_duplicates(inplace=True)
    venues['Price Range']=i+1
    venues_priced=venues_priced.append(venues,ignore_index=True)

Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Ditmas Park
Wingate
Rugby
Remsen Village
New Lots
Paerdegat Basin
Mill Basin
Fulton Ferry
Vinegar Hill
Weeksville
Broadway Junction
Dumbo
Homecrest
Highland Park
Madison
Erasmus
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heig

In [24]:
venues_priced.tail()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
741     South Side              40.710861              -73.958001   
742     South Side              40.710861              -73.958001   
743  Fort Hamilton              40.614768              -74.031979   
744       New Lots              40.662744              -73.885118   
745   Fulton Ferry              40.703281              -73.995508   

                       Venue  Venue Latitude  Venue Longitude  \
741  Peter Luger Steak House       40.709958       -73.962291   
742          Maison Premiere       40.714239       -73.961512   
743        Embers Steakhouse       40.616648       -74.033815   
744        Piggys Restaurant       40.666164       -73.882599   
745           The River Café       40.703754       -73.994834   

          Venue Category  Price Range  
741           Steakhouse            4  
742   Seafood Restaurant            4  
743           Steakhouse            4  
744   Spanish Restaurant            4  
745  American Restaurant            4

In [25]:
colors_array2 = cm.rainbow(np.linspace(0, 1, 4))
rainbow2 = [colors.rgb2hex(i) for i in colors_array2]

In [26]:
# plot the different price range on a map

map_venues_priced = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood, name, price in zip(venues_priced['Venue Latitude'], venues_priced['Venue Longitude'], venues_priced['Neighborhood'], venues_priced['Venue'], venues_priced['Price Range']):
    label = '{}, {}'.format(neighborhood, name)
    label = folium.Popup(label, parse_html=True)
    
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color=rainbow2[price-1],
        fill=True,
        fill_color=rainbow2[price-1],
        fill_opacity=0.4,
        parse_html=False).add_to(map_venues_priced)  
    
map_venues_priced

## as initial examination, use k means to cluster the restaurants into 4 groups, based on the neighbourhood, category and price range

In [27]:
venues_onehot=pd.get_dummies(venues_priced[['Venue Category','Neighborhood']],prefix="", prefix_sep="")
venues_onehot['Price Range']=venues_priced['Price Range']
venues_onehot['Venue']=venues_priced['Venue']
fixed_columns = [venues_onehot.columns[-1]] + list(venues_onehot.columns[:-1])
venues_onehot = venues_onehot[fixed_columns]

venues_onehot.head()

Venue  African Restaurant  American Restaurant  \
0           Bagel Boy                   0                    0   
1            Cinnabon                   0                    0   
2  My Thai Restaurant                   0                    0   
3      Pearl of China                   0                    0   
4          McDonald's                   0                    0   

   Arepa Restaurant  Argentinian Restaurant  Asian Restaurant  BBQ Joint  \
0                 0                       0                 0          0   
1                 0                       0                 0          0   
2                 0                       0                 0          0   
3                 0                       0                 0          0   
4                 0                       0                 0          0   

   Bagel Shop  Bakery  Breakfast Spot  Burger Joint  Burrito Place  Café  \
0           1       0               0             0              0     0   
1           0       0               0             0              0     0   
2           0       0               0             0              0     0   
3           0       0               0             0              0     0   
4           0       0               0             0              0     0   

   Cajun / Creole Restaurant  Caribbean Restaurant  Chinese Restaurant  \
0                          0                     0                   0   
1                          0                     0                   0   
2                          0                     0                   0   
3                          0                     0                   1   
4                          0                     0                   0   

   Creperie  Cuban Restaurant  Deli / Bodega  Dim Sum Restaurant  Diner  \
0         0                 0              0                   0      0   
1         0                 0              0                   0      0   
2         0                 0              0                   0      0   
3         0                 0              0                   0      0   
4         0                 0              0                   0      0   

   Donut Shop  Dumpling Restaurant  Eastern European Restaurant  \
0           0                    0                            0   
1           0                    0                            0   
2           0                    0                            0   
3           0                    0                            0   
4           0                    0                            0   

   Ethiopian Restaurant  Falafel Restaurant  Fast Food Restaurant  Food  \
0                     0                   0                     0     0   
1                     0                   0                     0     0   
2                     0                   0                     0     0   
3                     0                   0                     0     0   
4                     0                   0                     1     0   

   Food Court  Food Truck  French Restaurant  Fried Chicken Joint  Gastropub  \
0           0           0                  0                    0          0   
1           0           0                  0                    0          0   
2           0           0                  0                    0          0   
3           0           0                  0                    0          0   
4           0           0                  0                    0          0   

   German Restaurant  Greek Restaurant  Hot Dog Joint  Indian Restaurant  \
0                  0                 0              0                  0   
1                  0                 0              0                  0   
2                  0                 0              0                  0   
3                  0                 0              0                  0   
4                  0                 0              0                  0   

   Israeli Restau

In [28]:
kclusters = 4

venues_clustering = venues_onehot.drop('Venue', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(venues_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 1, 2, 1, 2, 2, 2, 1, 1], dtype=int32)

In [29]:
venues_priced.insert(0, 'Cluster Labels', kmeans.labels_)
venues_merged=venues_priced.merge(venues_onehot,how='outer')
venues_merged.drop(['Neighborhood','Neighborhood Latitude','Neighborhood Longitude','Venue Category'],1,inplace=True)
venues_merged.head(10)

Cluster Labels                     Venue  Venue Latitude  Venue Longitude  \
0               1                 Bagel Boy       40.627896       -74.029335   
1               1                  Cinnabon       40.623156       -74.031459   
2               1        My Thai Restaurant       40.629160       -74.028689   
3               2            Pearl of China       40.624631       -74.030301   
4               1                McDonald's       40.622159       -74.027731   
5               1                McDonald's       40.622159       -74.027731   
6               1                McDonald's       40.598078       -73.961428   
7               1                McDonald's       40.598078       -73.961428   
8               2            Taste Of China       40.608834       -73.994117   
9               2  Panda Chinese Restaurant       40.611388       -73.990784   

   Price Range  African Restaurant  American Restaurant  Arepa Restaurant  \
0            1                   0                    0                 0   
1            1                   0                    0                 0   
2            1                   0                    0                 0   
3            1                   0                    0                 0   
4            1                   0                    0                 0   
5            1                   0                    0                 0   
6            1                   0                    0                 0   
7            1                   0                    0                 0   
8            1                   0                    0                 0   
9            1                   0                    0                 0   

   Argentinian Restaurant  Asian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                       0                 0          0           1       0   
1                       0                 0          0           0       0   
2                       0                 0          0           0       0   
3                       0                 0          0           0       0   
4                       0                 0          0           0       0   
5                       0                 0          0           0       0   
6                       0                 0          0           0       0   
7                       0                 0          0           0       0   
8                       0                 0          0           0       0   
9                       0                 0          0           0       0   

   Breakfast Spot  Burger Joint  Burrito Place  Café  \
0               0             0              0     0   
1               0             0              0     0   
2               0             0              0     0   
3               0             0              0     0   
4               0             0              0     0   
5               0             0              0     0   
6               0             0              0     0   
7               0             0              0     0   
8               0             0              0     0   
9               0             0              0     0   

   Cajun / Creole Restaurant  Caribbean Restaurant  Chinese Restaurant  \
0                          0                     0                   0   
1                          0                     0                   0   
2                          0                     0                   0   
3                          0                     0                   1   
4                          0                     0                   0   
5                          0                     0                   0   
6                          0                     0                   0   
7                          0                     0                   0   
8                          0                     0                   1   
9                          0                     0        

### visualise the resulting cluster

In [30]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
#x = np.arange(kclusters)
#ys = [i + x + (i*x)**2 for i in range(kclusters)]
#colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
#rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(venues_priced['Venue Latitude'], venues_priced['Venue Longitude'], venues_priced['Neighborhood'], venues_priced['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow2[cluster],
        fill=True,
        fill_color=rainbow2[cluster],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### now examine each cluster, grouped by the price range(s) present in the cluster

In [31]:
for i in range(kclusters):
    venues_grouped=venues_merged[venues_merged['Cluster Labels']==i].drop('Venue',1).groupby('Price Range').mean().reset_index()
    display(venues_grouped.sort_values(by=0,axis=1,ascending=False))

Venue Latitude  Price Range  North Side  South Side  Italian Restaurant  \
0       40.682067            2    0.130952    0.114286            0.097619   

   American Restaurant  Pizza Place  Mexican Restaurant  Fort Greene  \
0             0.092857     0.066667            0.059524     0.054762   

   Cobble Hill  Clinton Hill  Brooklyn Heights  Japanese Restaurant  \
0     0.054762      0.054762          0.054762             0.040476   

   Thai Restaurant     Diner     Dumbo  Downtown  Carroll Gardens  \
0         0.040476  0.035714  0.035714  0.035714         0.033333   

   French Restaurant  Prospect Heights  Park Slope  Greenpoint  Boerum Hill  \
0           0.033333          0.033333    0.033333    0.030952      0.02619   

   Bay Ridge  Middle Eastern Restaurant  Sushi Restaurant  Mill Basin  \
0    0.02619                    0.02381           0.02381     0.02381   

   Seafood Restaurant  Caribbean Restaurant  Restaurant  Indian Restaurant  \
0             0.02381               0.02381    0.021429           0.021429   

   Fulton Ferry  Korean Restaurant  Sandwich Place  Burger Joint  \
0      0.021429           0.021429        0.021429      0.019048   

   Latin American Restaurant  BBQ Joint  Asian Restaurant  Georgetown  \
0                   0.019048   0.019048          0.016667    0.016667   

   Fort Hamilton  Vegetarian / Vegan Restaurant  Brighton Beach  \
0       0.016667                       0.016667        0.014286   

   New American Restaurant  East Williamsburg  Breakfast Spot  \
0                 0.014286           0.014286        0.014286   

   Fried Chicken Joint  Windsor Terrace  Sheepshead Bay  Wings Joint  \
0             0.014286         0.014286        0.014286     0.011905   

   Ditmas Park  Fast Food Restaurant  Deli / Bodega  Vietnamese Restaurant  \
0     0.011905              0.011905       0.011905               0.011905   

   Red Hook    Bakery   Gowanus  Dim Sum Restaurant  Homecrest      Café  \
0  0.009524  0.009524  0.009524            0.009524   0.009524  0.009524   

   Arepa Restaurant  South American Restaurant  Creperie  Food Truck  \
0          0.009524                   0.009524  0.009524    0.009524   

   Williamsburg  Vinegar Hill  Spanish Restaurant  Taco Place  Kensington  \
0      0.009524      0.007143            0.007143    0.007143    0.007143   

   Ramen Restaurant  Turkish Restaurant  Bushwick  Sunset Park  \
0          0.007143            0.007143  0.004762     0.004762   

   Argentinian Restaurant  City Line  Borough Park  Cuban Restaurant  \
0                0.004762   0.004762      0.004762          0.004762   

   Flatbush  Eastern European Restaurant  Greek Restaurant  \
0  0.004762                     0.004762          0.004762   

   Ethiopian Restaurant  Gravesend  Bagel Shop  Bath Beach  \
0              0.004762   0.004762    0.004762    0.004762   

   Prospect Park South  Mediterranean Restaurant  Polish Restaurant  \
0             0.004762                  0.004762           0.004762   

   Russian Restaurant  Bensonhurst  Southern / Soul Food Restaurant  \
0            0.004762     0.004762                         0.004762   

   Remsen Village   Erasmus   Midwood  Prospect Lefferts Gardens     Rugby  \
0        0.004762  0.002381  0.002381                   0.002381  0.002381   

   Highland Park  Gerritsen Beach  African Restaurant  Burrito Place  \
0       0.002381         0.002381            0.002381       0.002381   

   East New York  Tapas Restaurant  Cajun / Creole Restaurant  \
0       0.002381          0.002381                   0.002381   

   Falafel Restaurant  Food Court  Gastropub  German Restaurant  \
0            0.002381    0.002381   0.002381           0.002381   

   Israeli Restaurant  Shanghai Restaurant  Taiwanese Restaurant  Salad Place  \
0            0.002381             0.002381              0.002381     0.002381   

   Brownsville  Coney Island  East Flatbush  Cypress Hills  Crown Heights  \
0     0.002381      0.002381 

Venue Latitude  Price Range  Cluster Labels  Donut Shop  Fort Hamilton  \
0        40.65692            1               1    0.764552        0.05363   

   Boerum Hill  Prospect Park South  Cypress Hills  Ditmas Park  Georgetown  \
0     0.052322             0.051014        0.05036     0.049052    0.048398   

   Broadway Junction  City Line  Manhattan Terrace  Clinton Hill  Downtown  \
0           0.045128   0.045128           0.044474      0.034663  0.033355   

   Pizza Place  Brooklyn Heights  East Williamsburg  Bath Beach  \
0     0.032701          0.032701           0.030085    0.029431   

   Fast Food Restaurant  Carroll Gardens  Homecrest  Brighton Beach  Flatbush  \
0              0.026815         0.025507   0.025507        0.024853  0.024853   

   Windsor Terrace  Starrett City  Ocean Hill   Gowanus  Gravesend  \
0         0.024199       0.023545    0.022891  0.022891   0.022891   

   Weeksville  Bagel Shop  Mill Basin  Burger Joint  Fried Chicken Joint  \
0    0.022891    0.022237    0.022237      0.019621             0.018313   

   North Side    Bakery  Middle Eastern Restaurant     Dumbo  South Side  \
0    0.014388  0.012426                   0.012426  0.011118    0.010464   

   Mexican Restaurant  Caribbean Restaurant  Latin American Restaurant  \
0            0.009156              0.009156                   0.007848   

   Fulton Ferry  Fort Greene  Williamsburg  Deli / Bodega    Diner  \
0      0.007194     0.007194       0.00654        0.00654  0.00654   

   Park Slope  Flatlands  Food Truck   Erasmus  Prospect Heights  \
0    0.005886   0.005886    0.005886  0.005886          0.005232   

   Dumpling Restaurant  Prospect Lefferts Gardens  Greenpoint  \
0             0.005232                   0.004578    0.004578   

   Falafel Restaurant  New Lots  Sunset Park  Sandwich Place  Cobble Hill  \
0            0.004578  0.003924     0.003924        0.003924     0.003924   

       Café  American Restaurant  Bushwick  Vinegar Hill  East New York  \
0  0.003924             0.003924  0.003924      0.003924        0.00327   

   Brownsville    Rugby  Remsen Village  Bay Ridge  Wingate  Burrito Place  \
0      0.00327  0.00327         0.00327    0.00327  0.00327        0.00327   

   Taco Place  Asian Restaurant  Thai Restaurant  Bensonhurst  Red Hook  \
0     0.00327           0.00327         0.002616     0.001962  0.001962   

   Restaurant  Kensington  Sheepshead Bay  Hot Dog Joint      Food  \
0    0.001962    0.001962        0.001308       0.001308  0.001308   

   Breakfast Spot  Indian Restaurant  Vietnamese Restaurant  Cuban Restaurant  \
0        0.001308           0.000654               0.000654          0.000654   

   Gerritsen Beach  Italian Restaurant   Madison  Korean Restaurant  \
0         0.000654            0.000654  0.000654           0.000654   

   Gastropub  Highland Park  Southern / Soul Food Restaurant  Coney Island  \
0   0.000654       0.000654                         0.000654      0.000654   

   Seafood Restaurant  Tibetan Restaurant  African Restaurant  \
0            0.000654            0.000654                 0.0   

   Arepa Restaurant  Argentinian Restaurant  BBQ Joint  \
0               0.0                     0.0        0.0   

   Cajun / Creole Restaurant  Chinese Restaurant  Dim Sum Restaurant  \
0                        0.0                 0.0                 0.0   

   French Restaurant  Midwood  Food Court  Ethiopian Restaurant  \
0                0.0      0.0         0.0                   0.0   

   Eastern European Restaurant  Creperie  Vegetarian / Vegan Restaurant  \
0                          0.0       0.0                            0.0   

   German Restaurant  Greek Restaurant  Wings Joint  Turkish Restaurant  \
0                0.0               0.0          0.0                 0.0   

   Bedford Stuyvesant  Tapas Restaurant  Borough Park  Taiwanese Restaurant  \
0                 0.0               0.0           0.0                   0.0   

   Sushi Restaurant  S

Venue Latitude  Cluster Labels  Chinese Restaurant  Price Range  Gravesend  \
0       40.651555               2                 1.0            1   0.153846   
1       40.649802               2                 1.0            2   0.000000   

   Clinton Hill  Bensonhurst  Greenpoint  City Line  Brooklyn Heights  \
0      0.076923     0.076923    0.051282   0.051282          0.051282   
1      0.000000     0.111111    0.000000   0.000000          0.000000   

   Fort Hamilton  Mill Basin  Windsor Terrace  Crown Heights   Erasmus  \
0       0.051282    0.051282         0.051282       0.025641  0.025641   
1       0.000000    0.111111         0.000000       0.000000  0.000000   

   Starrett City  Carroll Gardens  Kensington  Bushwick  Bay Ridge  \
0       0.025641         0.025641    0.025641  0.025641   0.025641   
1       0.000000         0.000000    0.111111  0.111111   0.111111   

   Bedford Stuyvesant  Bath Beach  Ocean Hill  Cobble Hill  Park Slope  \
0            0.025641    0.025641    0.025641     0.025641    0.025641   
1            0.000000    0.000000    0.000000     0.000000    0.111111   

   Prospect Lefferts Gardens  Boerum Hill  East Flatbush  Ditmas Park  \
0                   0.025641     0.025641       0.025641          0.0   
1                   0.000000     0.000000       0.000000          0.0   

   Coney Island  Cypress Hills  Downtown  Williamsburg  Brownsville  \
0           0.0            0.0       0.0           0.0          0.0   
1           0.0            0.0       0.0           0.0          0.0   

   Broadway Junction  Brighton Beach  Borough Park  Wings Joint  \
0                0.0             0.0           0.0          0.0   
1                0.0             0.0           0.0          0.0   

   Vietnamese Restaurant  Vegetarian / Vegan Restaurant  Dumbo  Fort Greene  \
0                    0.0                            0.0    0.0          0.0   
1                    0.0                            0.0    0.0          0.0   

   East New York  East Williamsburg  Vinegar Hill  Sunset Park  South Side  \
0            0.0                0.0           0.0          0.0    0.000000   
1            0.0                0.0           0.0          0.0    0.111111   

   Sheepshead Bay  Rugby  Remsen Village  Red Hook  Prospect Park South  \
0             0.0    0.0             0.0       0.0                  0.0   
1             0.0    0.0             0.0       0.0                  0.0   

   Prospect Heights  North Side  New Lots  Midwood  Manhattan Terrace  \
0               0.0         0.0       0.0      0.0                0.0   
1               0.0         0.0       0.0      0.0                0.0   

   Madison  Homecrest  Highland Park   Gowanus  Gerritsen Beach  Georgetown  \
0      0.0   0.000000            0.0  0.000000              0.0         0.0   
1      0.0   0.111111            0.0  0.111111              0.0         0.0   

   Turkish Restaurant  Weeksville  Flatlands  Flatbush  Fulton Ferry  \
0                 0.0         0.0        0.0       0.0           0.0   
1                 0.0         0.0        0.0       0.0           0.0   

   Thai Restaurant  Tibetan Restaurant  Tapas Restaurant  French Restaurant  \
0              0.0                 0.0               0.0                0.0   
1              0.0                 0.0               0.0                0.0   

   Food Truck  Food Court  Food  Fast Food Restaurant  Falafel Restaurant  \
0         0.0         0.0   0.0                   0.0                 0.0   
1         0.0         0.0   0.0                   0.0                 0.0   

   Ethiopian Restaurant  Eastern European Restaurant  Dumpling Restaurant  \
0                   0.0                          0.0                  0.0   
1                   0.0                          0.0                  0.0   

   Donut Shop  Diner  Dim Sum Restaurant  Deli / Bodega  Cuban Restaurant  \
0         0.0    0.0                 0.0            0.0               0.0   
1         0.0   

Venue Latitude  Price Range  Cluster Labels  American Restaurant  \
0       40.679232            3               3             0.168067   
1       40.687775            4               3             0.058824   

   Italian Restaurant  South Side  North Side  Japanese Restaurant  Bay Ridge  \
0            0.159664    0.134454    0.109244             0.109244    0.07563   
1            0.058824    0.205882    0.176471             0.000000    0.00000   

   Tapas Restaurant  Williamsburg  Fulton Ferry  Fort Greene  \
0           0.07563      0.058824      0.058824     0.058824   
1           0.00000      0.147059      0.029412     0.000000   

   French Restaurant  Seafood Restaurant  New American Restaurant   Gowanus  \
0            0.05042            0.050420                 0.042017  0.042017   
1            0.00000            0.117647                 0.029412  0.000000   

   Mexican Restaurant  Mill Basin     Dumbo  Cobble Hill  Pizza Place  \
0            0.042017    0.042017  0.042017     0.042017     0.033613   
1            0.029412    0.000000  0.000000     0.000000     0.000000   

   Taco Place  Clinton Hill  Boerum Hill  South American Restaurant  \
0    0.033613      0.033613     0.033613                   0.033613   
1    0.000000      0.000000     0.000000                   0.000000   

   Carroll Gardens  Park Slope  Breakfast Spot  Russian Restaurant  \
0         0.033613    0.033613        0.033613             0.02521   
1         0.029412    0.029412        0.000000             0.00000   

   Brooklyn Heights  Fort Hamilton  Sheepshead Bay  Mediterranean Restaurant  \
0           0.02521       0.025210        0.025210                  0.016807   
1           0.00000       0.029412        0.029412                  0.000000   

   Deli / Bodega  Restaurant  Georgetown   Madison  Chinese Restaurant  \
0       0.016807    0.016807    0.016807  0.016807            0.016807   
1       0.000000    0.000000    0.000000  0.000000            0.029412   

   Turkish Restaurant  Downtown   Erasmus  East Williamsburg  Red Hook  \
0            0.016807  0.016807  0.008403           0.008403  0.008403   
1            0.000000  0.000000  0.000000           0.000000  0.000000   

   Spanish Restaurant  Polish Restaurant  Steakhouse  Peruvian Restaurant  \
0            0.008403           0.008403    0.008403             0.008403   
1            0.117647           0.000000    0.147059             0.000000   

   Latin American Restaurant  Prospect Heights  Vinegar Hill  \
0                   0.008403          0.008403      0.008403   
1                   0.294118          0.029412      0.000000   

   German Restaurant  Gastropub  Borough Park  Brighton Beach  Greenpoint  \
0           0.008403   0.008403      0.008403        0.008403    0.008403   
1           0.000000   0.000000      0.029412        0.000000    0.000000   

   Homecrest  Crown Heights  Coney Island  Cypress Hills  Starrett City  \
0   0.008403       0.000000           0.0       0.000000       0.000000   
1   0.000000       0.029412           0.0       0.029412       0.029412   

   Sunset Park  Ditmas Park  City Line  Windsor Terrace  Manhattan Terrace  \
0          0.0          0.0        0.0              0.0                0.0   
1          0.0          0.0        0.0              0.0                0.0   

   Rugby  Ocean Hill  Kensington  Highland Park  Midwood  Gravesend  New Lots  \
0    0.0         0.0         0.0            0.0      0.0        0.0  0.000000   
1    0.0         0.0         0.0            0.0      0.0        0.0  0.058824   

   Gerritsen Beach  Bushwick  Remsen Village  Weeksville  \
0              0.0  0.000000             0.0         0.0   
1              0.0  0.029412             0.0         0.0   

   Prospect Lefferts Gardens  Flatlands  Prospect Park South  East New York  \
0                        0.0        0.0                  0.0       0.000000   
1                        0.0        0.0                  0.0       0.058824   

 

### some interesting observations can be made:
clusters are related to price ranges: cluster 0 is lower mid range, cluster 1 is mid range, cluster 2 is low range and cluster 3 is high.

cluster 1 contains only italian resturants.

cluster 2 has many donut shops.

### try a different clustering algorithm

In [32]:
from sklearn.cluster import SpectralClustering
from sklearn.cluster import AgglomerativeClustering

#sc = (n_clusters=kclusters, assign_labels="discretize",random_state=0).fit(venues_clustering)
ac=AgglomerativeClustering(n_clusters=kclusters).fit(venues_clustering)
#sc.labels_[0:10]
ac.labels_[0:10]

array([0, 0, 0, 0, 3, 3, 3, 3, 3, 3])

In [33]:
venues_priced['Cluster Labels']=ac.labels_

In [34]:
venues_priced.head()

Cluster Labels Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0               0    Bay Ridge              40.625801              -74.030621   
1               0    Bay Ridge              40.625801              -74.030621   
2               0    Bay Ridge              40.625801              -74.030621   
3               0    Bay Ridge              40.625801              -74.030621   
4               3    Bay Ridge              40.625801              -74.030621   

                Venue  Venue Latitude  Venue Longitude        Venue Category  \
0           Bagel Boy       40.627896       -74.029335            Bagel Shop   
1            Cinnabon       40.623156       -74.031459        Sandwich Place   
2  My Thai Restaurant       40.629160       -74.028689       Thai Restaurant   
3      Pearl of China       40.624631       -74.030301    Chinese Restaurant   
4          McDonald's       40.622159       -74.027731  Fast Food Restaurant   

   Price Range  
0            1  
1            1  
2            1  
3            1  
4            1

In [35]:
venues_merged=venues_priced.merge(venues_onehot,how='outer')
venues_merged.drop(['Neighborhood','Neighborhood Latitude','Neighborhood Longitude','Venue Category'],1,inplace=True)
venues_merged.head(10)

Cluster Labels                     Venue  Venue Latitude  Venue Longitude  \
0               0                 Bagel Boy       40.627896       -74.029335   
1               0                  Cinnabon       40.623156       -74.031459   
2               0        My Thai Restaurant       40.629160       -74.028689   
3               0            Pearl of China       40.624631       -74.030301   
4               3                McDonald's       40.622159       -74.027731   
5               3                McDonald's       40.622159       -74.027731   
6               3                McDonald's       40.598078       -73.961428   
7               3                McDonald's       40.598078       -73.961428   
8               3            Taste Of China       40.608834       -73.994117   
9               3  Panda Chinese Restaurant       40.611388       -73.990784   

   Price Range  African Restaurant  American Restaurant  Arepa Restaurant  \
0            1                   0                    0                 0   
1            1                   0                    0                 0   
2            1                   0                    0                 0   
3            1                   0                    0                 0   
4            1                   0                    0                 0   
5            1                   0                    0                 0   
6            1                   0                    0                 0   
7            1                   0                    0                 0   
8            1                   0                    0                 0   
9            1                   0                    0                 0   

   Argentinian Restaurant  Asian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                       0                 0          0           1       0   
1                       0                 0          0           0       0   
2                       0                 0          0           0       0   
3                       0                 0          0           0       0   
4                       0                 0          0           0       0   
5                       0                 0          0           0       0   
6                       0                 0          0           0       0   
7                       0                 0          0           0       0   
8                       0                 0          0           0       0   
9                       0                 0          0           0       0   

   Breakfast Spot  Burger Joint  Burrito Place  Café  \
0               0             0              0     0   
1               0             0              0     0   
2               0             0              0     0   
3               0             0              0     0   
4               0             0              0     0   
5               0             0              0     0   
6               0             0              0     0   
7               0             0              0     0   
8               0             0              0     0   
9               0             0              0     0   

   Cajun / Creole Restaurant  Caribbean Restaurant  Chinese Restaurant  \
0                          0                     0                   0   
1                          0                     0                   0   
2                          0                     0                   0   
3                          0                     0                   1   
4                          0                     0                   0   
5                          0                     0                   0   
6                          0                     0                   0   
7                          0                     0                   0   
8                          0                     0                   1   
9                          0                     0        

In [36]:
for i in range(kclusters):
    venues_grouped=venues_merged[venues_merged['Cluster Labels']==i].drop('Venue',1).groupby('Price Range').mean().reset_index()
    display(venues_grouped.sort_values(by=0,axis=1,ascending=False))

Venue Latitude  Price Range  South Side  American Restaurant  North Side  \
0       40.689538            1    0.333333             0.222222    0.222222   
1       40.678689            2    0.188034             0.115385    0.209402   
2       40.677185            3    0.169231             0.076923    0.169231   
3       40.682311            4    0.000000             0.000000    0.000000   

   Williamsburg  Taco Place  Bay Ridge  Burger Joint  \
0      0.185185    0.185185   0.148148      0.111111   
1      0.008547    0.008547   0.042735      0.012821   
2      0.046154    0.000000   0.138462      0.000000   
3      0.000000    0.000000   0.000000      0.000000   

   Middle Eastern Restaurant  Latin American Restaurant  Mexican Restaurant  \
0                   0.111111                   0.074074            0.074074   
1                   0.012821                   0.025641            0.034188   
2                   0.000000                   0.000000            0.015385   
3                   0.000000                   0.000000            0.000000   

   Dumpling Restaurant  Sandwich Place  Chinese Restaurant  Georgetown  \
0             0.074074        0.037037            0.037037    0.037037   
1             0.000000        0.000000            0.021368    0.029915   
2             0.000000        0.000000            0.030769    0.030769   
3             0.000000        0.000000            0.000000    0.000000   

   Kensington  Fort Hamilton  Thai Restaurant  Bagel Shop  Creperie  \
0    0.037037       0.037037         0.037037    0.037037  0.000000   
1    0.004274       0.017094         0.042735    0.000000  0.017094   
2    0.000000       0.000000         0.000000    0.000000  0.000000   
3    0.000000       0.000000         0.000000    0.000000  0.000000   

   Ditmas Park  Fulton Ferry  BBQ Joint  Fort Greene  Flatlands  Flatbush  \
0          0.0      0.000000   0.000000     0.000000        0.0       0.0   
1          0.0      0.012821   0.029915     0.059829        0.0       0.0   
2          0.0      0.000000   0.000000     0.061538        0.0       0.0   
3          0.0      0.000000   0.000000     0.000000        0.0       0.0   

   Erasmus  East Williamsburg  East New York  East Flatbush     Dumbo  \
0      0.0                0.0       0.000000            0.0  0.000000   
1      0.0                0.0       0.004274            0.0  0.012821   
2      0.0                0.0       0.000000            0.0  0.000000   
3      0.0                0.0       0.000000            0.0  0.000000   

   Downtown  Cypress Hills  Gerritsen Beach  Crown Heights  Coney Island  \
0  0.000000            0.0         0.000000            0.0           0.0   
1  0.012821            0.0         0.004274            0.0           0.0   
2  0.030769            0.0         0.000000            0.0           0.0   
3  0.000000            0.0         0.000000            0.0           0.0   

   Cobble Hill  Clinton Hill  City Line  Carroll Gardens  Bushwick  \
0     0.000000      0.000000   0.000000         0.000000       0.0   
1     0.094017      0.025641   0.008547         0.029915       0.0   
2     0.061538      0.015385   0.000000         0.046154       0.0   
3     0.000000      0.000000   0.000000         1.000000       0.0   

   Brownsville  Brooklyn Heights  Broadway Junction  Brighton Beach  \
0     0.000000          0.000000                0.0        0.000000   
1     0.004274          0.008547                0.0        0.025641   
2     0.000000          0.000000                0.0        0.000000   
3     0.000000          0.000000                0.0        0.000000   

   Asian Restaurant   Gowanus  Boerum Hill  Gravesend  Windsor Terrace  \
0          0.000000  0.000000     0.000000   0.000000         0.000000   
1          0.021368  0.021368     0.000000   0.008547         0.008547   
2          0.000000  0.061538     0.046154   0.000000         0.000000   
3          0.000000  0.000000     0.000000   0.000000         0.000

Venue Latitude  Price Range  Cluster Labels  Donut Shop  Pizza Place  \
0       40.675057            1               1     0.60177     0.070796   
1       40.685726            2               1     0.00000     0.098684   
2       40.691317            3               1     0.00000     0.000000   

   Boerum Hill  Downtown  Brooklyn Heights  Clinton Hill  Ditmas Park  \
0     0.067847  0.058997          0.058997      0.053097     0.047198   
1     0.065789  0.072368          0.131579      0.111842     0.032895   
2     0.000000  0.000000          0.200000      0.100000     0.000000   

   Prospect Park South  Georgetown  Broadway Junction  Fort Hamilton  \
0             0.044248    0.041298           0.038348       0.038348   
1             0.013158    0.000000           0.000000       0.013158   
2             0.000000    0.000000           0.000000       0.000000   

   Cypress Hills  Manhattan Terrace  City Line  Windsor Terrace  Burger Joint  \
0       0.038348           0.035398   0.035398         0.032448      0.032448   
1       0.000000           0.000000   0.000000         0.026316      0.019737   
2       0.000000           0.000000   0.000000         0.000000      0.000000   

   Chinese Restaurant    Bakery  Carroll Gardens  Bagel Shop     Dumbo  \
0            0.029499  0.029499         0.029499    0.026549  0.023599   
1            0.006579  0.013158         0.046053    0.013158  0.059211   
2            0.000000  0.000000         0.000000    0.000000  0.200000   

   Flatbush  Greenpoint  Bath Beach  Prospect Heights  Park Slope  \
0  0.023599    0.023599    0.023599          0.023599    0.023599   
1  0.013158    0.072368    0.000000          0.065789    0.098684   
2  0.000000    0.000000    0.000000          0.000000    0.100000   

   Caribbean Restaurant  Gravesend     Diner  Deli / Bodega  \
0              0.020649   0.020649  0.020649       0.020649   
1              0.065789   0.000000  0.052632       0.026316   
2              0.000000   0.000000  0.000000       0.100000   

   Middle Eastern Restaurant  Homecrest  Weeksville  Brighton Beach  \
0                   0.020649   0.017699    0.017699        0.017699   
1                   0.046053   0.000000    0.000000        0.000000   
2                   0.000000   0.000000    0.000000        0.000000   

   Starrett City  Mexican Restaurant  Ocean Hill  East Williamsburg  \
0       0.017699            0.017699    0.017699           0.017699   
1       0.000000            0.098684    0.000000           0.000000   
2       0.000000            0.000000    0.000000           0.000000   

   Mill Basin   Gowanus  Fulton Ferry  Dumpling Restaurant  \
0    0.017699  0.017699      0.014749             0.011799   
1    0.000000  0.000000      0.019737             0.000000   
2    0.000000  0.000000      0.200000             0.000000   

   Latin American Restaurant  Burrito Place  Fort Greene      Café  \
0                   0.011799       0.011799     0.011799  0.008850   
1                   0.013158       0.000000     0.052632  0.013158   
2                   0.000000       0.000000     0.100000  0.000000   

   Cobble Hill  Vinegar Hill  Fast Food Restaurant  Falafel Restaurant  \
0     0.008850      0.008850               0.00885            0.008850   
1     0.006579      0.013158               0.00000            0.006579   
2     0.000000      0.000000               0.00000            0.000000   

   North Side   Erasmus  Prospect Lefferts Gardens  Thai Restaurant  \
0    0.005900  0.005900                     0.0059         0.005900   
1    0.026316  0.006579                     0.0000         0.032895   
2    0.000000  0.100000                     0.0000         0.000000   

   Fried Chicken Joint  Food Truck  Breakfast Spot  East New York     Rugby  \
0               0.0059    0.005900        0.005900        0.00295  0.002950   
1               0.0000    0.013158        0.013158        0.00000  0.006579   
2               0.0000    0.000000        0.00000

Venue Latitude  Price Range  Cluster Labels  French Restaurant  \
0       40.699175            2               2           0.428571   
1       40.679509            3               2           0.136364   
2       40.687941            4               2           0.000000   

   Korean Restaurant  South Side     Diner  Williamsburg  Boerum Hill  \
0           0.285714    0.285714  0.285714      0.285714     0.142857   
1           0.000000    0.113636  0.000000      0.090909     0.022727   
2           0.000000    0.212121  0.000000      0.151515     0.000000   

   Downtown  Fort Greene  Erasmus  East Williamsburg  Flatbush  Coney Island  \
0  0.142857     0.142857      0.0           0.000000  0.000000           0.0   
1  0.000000     0.045455      0.0           0.022727  0.000000           0.0   
2  0.000000     0.000000      0.0           0.000000  0.030303           0.0   

   East Flatbush     Dumbo  Ditmas Park  Cypress Hills  Crown Heights  \
0            0.0  0.000000          0.0       0.000000       0.000000   
1            0.0  0.068182          0.0       0.000000       0.000000   
2            0.0  0.000000          0.0       0.030303       0.030303   

   East New York  Carroll Gardens  Cobble Hill  Clinton Hill  City Line  \
0       0.000000         0.000000     0.000000      0.000000        0.0   
1       0.000000         0.022727     0.022727      0.045455        0.0   
2       0.060606         0.000000     0.000000      0.000000        0.0   

   Bushwick  Brownsville  Brooklyn Heights  Broadway Junction  Brighton Beach  \
0  0.000000          0.0          0.000000                0.0        0.000000   
1  0.000000          0.0          0.022727                0.0        0.022727   
2  0.030303          0.0          0.000000                0.0        0.000000   

   Borough Park  Bensonhurst  Bedford Stuyvesant  Bay Ridge  Bath Beach  \
0      0.000000          0.0                 0.0        0.0         0.0   
1      0.022727          0.0                 0.0        0.0         0.0   
2      0.030303          0.0                 0.0        0.0         0.0   

   Wings Joint  Flatlands  Georgetown  Fort Hamilton  Ocean Hill  \
0          0.0        0.0         0.0       0.000000         0.0   
1          0.0        0.0         0.0       0.068182         0.0   
2          0.0        0.0         0.0       0.030303         0.0   

   Windsor Terrace  Weeksville  Vinegar Hill  Sunset Park  Starrett City  \
0              0.0         0.0      0.000000          0.0       0.000000   
1              0.0         0.0      0.022727          0.0       0.000000   
2              0.0         0.0      0.000000          0.0       0.030303   

   Sheepshead Bay  Rugby  Remsen Village  Red Hook  Prospect Park South  \
0        0.000000    0.0             0.0       0.0                  0.0   
1        0.045455    0.0             0.0       0.0                  0.0   
2        0.030303    0.0             0.0       0.0                  0.0   

   Prospect Lefferts Gardens  Prospect Heights  Park Slope  North Side  \
0                        0.0          0.000000    0.000000    0.000000   
1                        0.0          0.022727    0.068182    0.045455   
2                        0.0          0.030303    0.030303    0.181818   

   Fulton Ferry  New Lots  Mill Basin  Midwood  Manhattan Terrace   Madison  \
0      0.000000  0.000000         0.0      0.0                0.0  0.000000   
1      0.113636  0.000000         0.0      0.0                0.0  0.022727   
2      0.030303  0.060606         0.0      0.0                0.0  0.000000   

   Kensington  Homecrest  Highland Park  Greenpoint  Gravesend   Gowanus  \
0         0.0   0.000000            0.0    0.000000        0.0  0.000000   
1         0.0   0.022727            0.0    0.022727        0.0  0.022727   
2         0.0   0.000000            0.0    0.000000        0.0  0.000000   

   Gerritsen Beach  Vegetarian / Vegan Restaurant  Vietnamese Restaurant  \
0              0.0

Venue Latitude  Cluster Labels  Price Range  Donut Shop  Fort Hamilton  \
0       40.650898               3            1    0.802829       0.058236   
1       40.677175               3            2    0.000000       0.027778   

   Cypress Hills  Prospect Park South  City Line  Ditmas Park  Georgetown  \
0       0.053245             0.052413   0.049085     0.049085    0.049085   
1       0.027778             0.000000   0.000000     0.000000    0.000000   

   Boerum Hill  Manhattan Terrace  Broadway Junction  East Williamsburg  \
0     0.048253           0.046589           0.046589           0.033278   
1     0.000000           0.000000           0.000000           0.166667   

   Clinton Hill  Fast Food Restaurant  Bath Beach  Gravesend  Homecrest  \
0      0.031614              0.031614    0.031614   0.028286   0.027454   
1      0.000000              0.138889    0.055556   0.000000   0.000000   

   Brooklyn Heights  Brighton Beach  Starrett City  Downtown  Flatbush  \
0          0.026622        0.026622        0.02579   0.02579  0.024958   
1          0.027778        0.000000        0.00000   0.00000  0.000000   

   Mill Basin  Ocean Hill  Carroll Gardens   Gowanus  Weeksville  \
0    0.024958    0.024958         0.024958  0.024126    0.024126   
1    0.000000    0.000000         0.000000  0.000000    0.000000   

   Windsor Terrace  Chinese Restaurant  Pizza Place  Fried Chicken Joint  \
0         0.023295            0.023295     0.021631             0.021631   
1         0.000000            0.083333     0.055556             0.111111   

   Bagel Shop  Burger Joint  North Side  Middle Eastern Restaurant    Bakery  \
0    0.019967      0.013311    0.011647                   0.007488  0.007488   
1    0.000000      0.055556    0.055556                   0.000000  0.000000   

      Dumbo  Flatlands   Erasmus  Caribbean Restaurant  Food Truck  \
0  0.007488   0.007488  0.006656              0.005824    0.005824   
1  0.083333   0.000000  0.000000              0.000000    0.055556   

   Fort Greene  Bushwick  Bensonhurst  Fulton Ferry  Mexican Restaurant  \
0     0.005824  0.005824     0.004992      0.004992            0.004992   
1     0.000000  0.083333     0.027778      0.083333            0.055556   

   Latin American Restaurant  Sunset Park  South Side  \
0                   0.004992     0.004992    0.004992   
1                   0.000000     0.000000    0.055556   

   Prospect Lefferts Gardens  Williamsburg  New Lots  Remsen Village  Wingate  \
0                   0.004992       0.00416   0.00416        0.004160  0.00416   
1                   0.027778       0.00000   0.00000        0.055556  0.00000   

   Asian Restaurant  Sandwich Place  Brownsville     Rugby  \
0           0.00416        0.003328     0.003328  0.003328   
1           0.00000        0.055556     0.000000  0.000000   

   Falafel Restaurant  Cobble Hill  East New York  Restaurant     Diner  \
0            0.003328     0.003328       0.003328    0.002496  0.002496   
1            0.000000     0.000000       0.000000    0.055556  0.000000   

       Café  Vinegar Hill  Deli / Bodega  Kensington  Red Hook  \
0  0.002496      0.002496       0.002496    0.002496  0.002496   
1  0.000000      0.027778       0.000000    0.083333  0.000000   

   Dumpling Restaurant  Park Slope  Bay Ridge  Sheepshead Bay      Food  \
0             0.001664    0.001664   0.001664        0.001664  0.001664   
1             0.000000    0.000000   0.055556        0.000000  0.000000   

   East Flatbush  Italian Restaurant   Madison  Seafood Restaurant  \
0       0.000832            0.000832  0.000832            0.000832   
1       0.000000            0.027778  0.000000            0.000000   

   Hot Dog Joint  Indian Restaurant  Highland Park  Greenpoint  Crown Heights  \
0       0.000832           0.000832       0.000832    0.000832       0.000832   
1       0.000000           0.083333       0.000000    0.000000       0.000000   

   Coney Island  Thai Restaurant  Gerritsen

In [105]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
#x = np.arange(kclusters)
#ys = [i + x + (i*x)**2 for i in range(kclusters)]
#colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
#rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(venues_priced['Venue Latitude'], venues_priced['Venue Longitude'], venues_priced['Neighborhood'], venues_priced['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow2[cluster],
        fill=True,
        fill_color=rainbow2[cluster],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

other clustering methods results in clusters that are less interpretable.

## Now try use different classification algorithms on the dataset to predict prices.

In [38]:
#first we need to prep the dataset into a training set and a test set.
from sklearn.model_selection import train_test_split
X=venues_merged.drop(['Cluster Labels','Venue'],1)
y=venues_merged['Price Range']
X=X.drop('Price Range',1)
train_x, test_x, train_y, test_y = train_test_split(X,y,test_size=0.2,stratify=y)

In [39]:
train_x.head()

Venue Latitude  Venue Longitude  African Restaurant  \
1913       40.711248       -73.961445                   0   
1401       40.576163       -73.990963                   0   
1292       40.708515       -73.958186                   0   
456        40.598100       -73.997225                   0   
1474       40.644880       -73.958007                   0   

      American Restaurant  Arepa Restaurant  Argentinian Restaurant  \
1913                    0                 0                       0   
1401                    0                 0                       0   
1292                    0                 0                       0   
456                     0                 0                       0   
1474                    0                 0                       0   

      Asian Restaurant  BBQ Joint  Bagel Shop  Bakery  Breakfast Spot  \
1913                 0          0           0       0               0   
1401                 0          0           0       0               0   
1292                 0          0           0       0               0   
456                  0          0           0       0               0   
1474                 0          0           0       0               0   

      Burger Joint  Burrito Place  Café  Cajun / Creole Restaurant  \
1913             0              0     0                          0   
1401             0              0     0                          0   
1292             0              0     0                          0   
456              0              0     0                          0   
1474             0              0     0                          0   

      Caribbean Restaurant  Chinese Restaurant  Creperie  Cuban Restaurant  \
1913                     0                   0         0                 0   
1401                     0                   0         0                 0   
1292                     0                   0         0                 0   
456                      0                   0         0                 0   
1474                     0                   0         0                 0   

      Deli / Bodega  Dim Sum Restaurant  Diner  Donut Shop  \
1913              0                   0      0           0   
1401              0                   0      0           0   
1292              0                   0      0           0   
456               0                   0      0           1   
1474              0                   0      0           0   

      Dumpling Restaurant  Eastern European Restaurant  Ethiopian Restaurant  \
1913                    0                            0                     0   
1401                    0                            0                     0   
1292                    0                            0                     0   
456                     0                            0                     0   
1474                    0                            0                     0   

      Falafel Restaurant  Fast Food Restaurant  Food  Food Court  Food Truck  \
1913                   0                     0     0           0           0   
1401                   0                     0     0           0           0   
1292                   0                     0     0           0           0   
456                    0                     0     0           0           0   
1474                   0                     0     0           0           0   

      French Restaurant  Fried Chicken Joint  Gastropub  German Restaurant  \
1913                  0                    1          0                  0   
1401                  0                    1          0                  0   
1292                  0                    0          0                  0   
456                   0                    0          0                  0   
1474                  0                    0          0                  0   

      Greek Restaurant  Hot Dog Joint  Indian Restaurant  Israeli Restaurant  \

In [45]:
# the data is not normalized, especially the location data
from sklearn.preprocessing import StandardScaler
# use a pipeline 
from sklearn.pipeline import make_pipeline
# use a grid search also
from sklearn.model_selection import GridSearchCV
# import the potential classifiers 
from sklearn.neural_network import MLPClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.tree import DecisionTreeClassifier

pipe=make_pipeline(StandardScaler(),SVC())

parameters=[{'svc__kernel': ['rbf'], 'svc__gamma': ['scale',1e-3, 1e-4],'svc__C': [1, 10, 100, 1000]}]

clf=GridSearchCV(pipe,parameters,cv=5).fit(train_x,train_y)


In [46]:
clf.best_params_

{'svc__C': 1, 'svc__gamma': 0.001, 'svc__kernel': 'rbf'}

In [47]:
clf.best_score_

0.838953488372093

In [50]:
# now repeat the same for other classifiers
# decision tree
pipe=make_pipeline(StandardScaler(),DecisionTreeClassifier())

parameters=[{'decisiontreeclassifier__criterion': ['entropy','gini'], 'decisiontreeclassifier__max_depth': [6,8,10,12,14,None]}]

clf=GridSearchCV(pipe,parameters,cv=5).fit(train_x,train_y)

print('the best parameters are:', clf.best_params_)
print('the best score is:', clf.best_score_)

the best parameters are: {'decisiontreeclassifier__criterion': 'gini', 'decisiontreeclassifier__max_depth': None}
the best score is: 0.8697674418604653


In [54]:
# now repeat the same for other classifiers
# k nearest neighbors
pipe=make_pipeline(StandardScaler(),KNeighborsClassifier())

parameters=[{'kneighborsclassifier__n_neighbors': [14,15,16], 'kneighborsclassifier__p': [1,2], 'kneighborsclassifier__weights':['uniform','distance']}]

clf=GridSearchCV(pipe,parameters,cv=5).fit(train_x,train_y)

print('the best parameters are:', clf.best_params_)
print('the best score is:', clf.best_score_)

the best parameters are: {'kneighborsclassifier__n_neighbors': 16, 'kneighborsclassifier__p': 2, 'kneighborsclassifier__weights': 'distance'}
the best score is: 0.8488372093023256


In [56]:
# now repeat the same for other classifiers
# multi layer perceptron
pipe=make_pipeline(StandardScaler(),MLPClassifier())

parameters=[{'mlpclassifier__solver': ['adam'], 'mlpclassifier__alpha': [1e-3,1e-4,1e-5], 'mlpclassifier__learning_rate':['constant'], 'mlpclassifier__max_iter':[1000]}]

clf=GridSearchCV(pipe,parameters,cv=5).fit(train_x,train_y)

print('the best parameters are:', clf.best_params_)
print('the best score is:', clf.best_score_)

the best parameters are: {'mlpclassifier__alpha': 0.001, 'mlpclassifier__learning_rate': 'constant', 'mlpclassifier__max_iter': 1000, 'mlpclassifier__solver': 'adam'}
the best score is: 0.8401162790697674


In [71]:
# now intialise the different classifiers based on their optimal parameters and pass through the test set
from sklearn.metrics import accuracy_score

svc=SVC(C= 1, gamma= 0.001, kernel= 'rbf').fit(train_x,train_y)
y_pred_svc=svc.predict(test_x)
acc_svc=accuracy_score(test_y,y_pred_svc)
acc_svc

0.727906976744186

In [70]:
knn=KNeighborsClassifier(n_neighbors=16, p= 2, weights='distance').fit(train_x,train_y)
y_pred_knn=knn.predict(test_x)
acc_knn=accuracy_score(test_y,y_pred_knn)
acc_knn

0.8767441860465116

In [72]:
dt=DecisionTreeClassifier().fit(train_x,train_y)
y_pred_dt=dt.predict(test_x)
acc_dt=accuracy_score(test_y,y_pred_dt)
acc_dt

0.872093023255814

In [73]:
mlp=MLPClassifier(alpha=0.001,max_iter=1000).fit(train_x,train_y)
y_pred_mlp=mlp.predict(test_x)
acc_mlp=accuracy_score(test_y,y_pred_mlp)
acc_mlp

0.8488372093023255

In [74]:
# make a dataframe to store the test results.

results=pd.DataFrame({'classifier':['SVC','KNN','DecisionTree','MLP'],'test accuracy':[acc_svc,acc_knn,acc_dt,acc_mlp]})



In [75]:
results

classifier  test accuracy
0           SVC       0.727907
1           KNN       0.876744
2  DecisionTree       0.872093
3           MLP       0.848837

KNN and decision tree both performed well.